In [ ]:
# compare labels

In [2]:
library(dplyr)
library(ggplot2)

In [3]:
# list of stages and samples
stages = rep(c('stage9', 'stage13', 'stage16'), each = 3)
samples = paste0('sample', rep(1:3, 3))

In [4]:
list1 = c('Qiu_Seurat_label_transfer', 'Asp_celltypes', 'Hill_celltypes',
          'Mantri_Seurat_label_transfer', 'Feng_celltypes', 'Knight-Schrijver_celltypes')

In [5]:
# load data
totaldf = c()
for(ii in 1:length(samples)){
    sampleid = ii
    for(jj in 1:length(list1)){
        temp = read.delim(paste0('annotations/', stages[sampleid], '_', samples[sampleid], '_', list1[jj], '.csv'), 
                          sep = ',')
        if(jj==1){
            newdf = data.frame(stage = stages[sampleid], sample = samples[sampleid], barcode = temp$barcode,
                              Qiu = temp$class)
        }else if(jj==4){        
            ids = match(newdf$barcode, rownames(temp))
            newdf <- cbind(newdf, temp$class[ids])
        }else if(jj==6){
            ids = match(newdf$barcode, temp$barcode)
            newdf <- cbind(newdf, temp$class[ids])            
        }else{
            ids = match(newdf$barcode, rownames(temp))
            newdf <- cbind(newdf, temp$predicted[ids])
        }
    }
    colnames(newdf)[5:9] = c('Asp', 'Hill', 'Mantri', 'Feng', 'Knight_Schrijver')
    totaldf = rbind(totaldf, newdf)
}
dim(totaldf)
totaldf[1,]

[1] 80893     9

stage  sample  barcode                                     Qiu         Asp
1 stage9 sample1 stage9_sample1_9_sample1_AAACCCAAGACCATGG-1 Endothelium NA 
  Hill Mantri Feng Knight_Schrijver
1 NA   NA     NA   NA

In [6]:
# save
write.table(totaldf, file = 'lizard_celltype_annotations.csv', sep = ',', 
            row.names = F, col.names = T, quote = F)

In [7]:
# add consensus types
tab1 = read.delim('~/septation/shared_consensus_types.csv', sep = ',')
unique(tab1$consensus_type)
tab1[1:2,]

df1 = totaldf
for(ii in 4:9){
    df1[,ii] <- tab1$consensus_type[match(df1[,ii], tab1$celltype)]
}
df1[1:2,]

[1] "Endothelial_cell"   "Cardiomyocyte"      "Myeloid_cell"      
 [4] "Mes_progenitor"     "Lymphoid_cell"      "Fibroblast"        
 [7] "Epithelial_cell"    "Neural_crest"       "Hepatocyte"        
[10] "Cardiac_progenitor" "unassigned"

celltype       study consensus_type  
1 Endothelium    Qiu   Endothelial_cell
2 Cardiomyocytes Qiu   Cardiomyocyte

stage  sample  barcode                                     Qiu             
1 stage9 sample1 stage9_sample1_9_sample1_AAACCCAAGACCATGG-1 Endothelial_cell
2 stage9 sample1 stage9_sample1_9_sample1_AAACCCAAGTAACGAT-1 Myeloid_cell    
  Asp Hill Mantri Feng Knight_Schrijver
1 NA  NA   NA     NA   NA              
2 NA  NA   NA     NA   NA

In [8]:
# filter row-wise
df1$consensus_type = 'unassigned'
pb = txtProgressBar(min = 0, max = dim(df1)[1], initial = 0)

for(ii in 1:dim(df1)[1]){
    vec1 = unlist(df1[ii,4:9])
    names(vec1) = NULL
    vec1 = vec1[which(!is.na(vec1) & vec1!='unassigned')]
    if(length(vec1)){
        df1$consensus_type[ii] = tail(names(sort(table(vec1))), 1)
    }
    setTxtProgressBar(pb, ii)
}
df1[1:3,]
totaldf$consensus_type = df1$consensus_type

stage  sample  barcode                                     Qiu             
1 stage9 sample1 stage9_sample1_9_sample1_AAACCCAAGACCATGG-1 Endothelial_cell
2 stage9 sample1 stage9_sample1_9_sample1_AAACCCAAGTAACGAT-1 Myeloid_cell    
3 stage9 sample1 stage9_sample1_9_sample1_AAACCCAAGTATGACA-1 Mes_progenitor  
  Asp Hill Mantri Feng Knight_Schrijver consensus_type  
1 NA  NA   NA     NA   NA               Endothelial_cell
2 NA  NA   NA     NA   NA               Myeloid_cell    
3 NA  NA   NA     NA   NA               Mes_progenitor

In [9]:
# save
write.table(totaldf, file = 'lizard_celltype_annotations.csv', sep = ',', 
            row.names = F, col.names = T, quote = F)